In [1]:
from itertools import chain

import zarr
import numpy as np
import pandas as pd

from neuclease.dvid import *
from neuclease.util import *

import hvplot.pandas

In [2]:
from neuclease import configure_default_logging
configure_default_logging()

In [3]:
del vnc_seg
del vnc_master

In [29]:
new_seg = ('emdata5.janelia.org:8400', find_master('emdata5.janelia.org:8400'), 'segmentation')
box_s6 = round_box(fetch_volume_box(*new_seg), 2**6) // 2**6

vol_s6 = fetch_labelmap_voxels_chunkwise(*new_seg, box_s6, scale=6, supervoxels=True)

[2021-02-16 12:20:59,121] INFO Fetching compressed chunks



[2021-02-16 12:21:27,945] INFO Inflating chunks


In [7]:
# Notes:
# - 16nm!
# - 1:oob 2:trachea 3:glia 4:cell bodies 5:neuropil
s = zarr.NestedDirectoryStore('/nrs/flyem/vnc/vnc-v3-masks-16nm.zarr')
f = zarr.open(store=s, mode='r')
dset = f['s5']
Z, Y, X = dset.shape
print(Z, Y, X)

642 438 335


In [14]:
np.prod(f['s0'].shape) / 1e12 * (2**3) # convert to 8nm voxels

198.102852180992

In [16]:
%time mask_s6 = f['s5'][:] # actually s6, relative to the 8nm data

CPU times: user 534 ms, sys: 184 ms, total: 718 ms
Wall time: 652 ms


In [17]:
mask_s6.shape

(1285, 876, 671)

In [20]:
((mask_s6 >= 2) & (mask_s6 != 3)).sum() * (2**6)**3 / 1e12

25.100063604736

In [40]:
syn_df, partner_df = fetch_synapses_in_batches(*new_seg[:2], 'synapses', processes=32)

if (syn_df[[*'zyx']].iloc[0] == 0).all():
    # drop 'fake' synapse for partnerless tbars
    syn_df = syn_df[[*'zyx', 'kind', 'conf']].iloc[1:].copy()

In [48]:
syn_df['body'] = fetch_labels_batched(*new_seg, syn_df[[*'zyx']].values, processes=32)

[2021-02-16 12:33:32,221] INFO Pre-sorting 9842292 coordinates by block index...
[2021-02-16 12:33:35,685] INFO Pre-sorting 9842292 coordinates by block index took 0:00:03.463860
[2021-02-16 12:33:35,917] INFO Fetching labels from DVID...


[2021-02-16 12:53:35,403] INFO Fetching labels from DVID took 0:19:59.485641


In [54]:
body_synapse_counts = syn_df.groupby('body').size()

In [58]:
tbar_counts = body_synapse_counts.sort_values(ascending=False).rename('tbars').to_frame().query('body != 0').copy()

In [59]:
tbar_counts['cumulative_tbars'] = tbar_counts['tbars'].cumsum()
tbar_counts['cumulative_frac'] = tbar_counts['cumulative_tbars'] / tbar_counts['tbars'].sum()

In [63]:
tbar_counts['cumulative_frac'].reset_index(drop=True).iloc[:100_000].hvplot(title='bodywise cumulative tbar coverage')

:Curve   [index]   (cumulative_frac)

In [21]:
top10k = pd.read_csv('/groups/flyem/data/scratchspace/flyemflows/vnc-fullseg/february/large-and-mutated-sizes-cd304d.csv').iloc[:10_000]

In [23]:
top10k['size'].sum() / 1e12

14.894853162043

In [31]:
bodies = pd.Series(list(set(range(10_000, 100_000)) | set(top10k['body'].tolist())), name='body').sample(frac=1.0)
top_sizes = fetch_sizes(*new_seg, bodies, processes=32, batch_size=100)

In [36]:
top90k = top_sizes.sort_values(ascending=False).iloc[:90_000]

In [37]:
top90k

body
10000     39532181744
10001     33442837987
10002     29336983880
10006     17256755675
100043    16553123199
             ...     
95679               0
95361               0
82261               0
84627               0
87640               0
Name: size, Length: 90000, dtype: int64

In [38]:
fetch_sizes(*new_seg, [87640])

body
87640    0
Name: size, dtype: int64

In [49]:
big_garbage = [
        "10006",
        "10008",
        "10026",
        "10027",
        "10028",
        "10030",
        "10032",
        "10033",
        "10034",
        "10035",
        "10036",
        "10037",
        "10038",
        "10040",
        "10041",
        "10043",
        "10044",
        "10045",
        "10046",
        "10078",
        "10079",
        "10080",
        "10081"
      ]
big_garbage = [*map(int, big_garbage)]

TypeError: int() argument must be a string, a bytes-like object or a number, not 'list'

In [ ]:
print(big_garbage)